In [67]:
# Download test pdf file. 

# ! pip install requests
# ! pip install langchain
# ! pip install pypdf
# ! pip install pdfminer.six
# ! pip install bs4
# ! pip install sentence_transformers

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 8.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.0/6.0 MB 11.2 MB/s eta 0:00:00a 0:00:01
  Obtaining dependency information for scikit-learn from https://files.pythonhosted.org/packages/d4/61/966d3238f6cbcbb13350d31bd0accfc5efdf9e349cd2a42d9761b8b67a18/scikit_learn-1.3.0-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata
  Obtaining dependency information for scipy from https://files.pythonhosted.org/packages/a3/d3/f88285098505c8e5d141678a24bb9620d902c683f11edc1eb9532b02624e/scipy-1.11.2-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.1/59.1 kB 10.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 11.4 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 12.2 MB

In [1]:
target_pdf_file_uri = "https://www.kbinsure.co.kr/CG802030003.ec?fileNm=20120401_10101_1.pdf"

In [2]:
from langchain.document_loaders import PyPDFLoader

loader = PyPDFLoader(target_pdf_file_uri)
pages = loader.load_and_split()

In [3]:
import os

PROJECT_NUMBER = os.getenv("PROJECT_NUMBER")
VERTEX_AI_LOCATION = "us-central1"



In [4]:
from google.auth import default

# Without Scopes, you will see the error. 
credentials, _ = default(scopes=["https://www.googleapis.com/auth/cloud-platform"])

In [5]:
import vertexai

vertexai.init(project=PROJECT_NUMBER, location=VERTEX_AI_LOCATION, credentials=credentials)
parameters = {
    "temperature" : 0.2,
    "max_output_tokens" : 1024, 
    "top_p": 0.8, 
    "top_k" : 10
}



In [6]:
from vertexai.preview.language_models import TextGenerationModel

model = TextGenerationModel.from_pretrained("text-bison-32k")

In [7]:
prev_content = ""
CONTENT_LENGTH_SIZE = 30000

PROMPT_DOC_PARSING = "split the Contents inside the ``` quote marks into appropriate phrases with hierarchycal section number in csv format. \nFormat : section_number, content_text \nExample Contents :  제1조(보험계약의 성립) \n① 보험계약은 보험계약자의 청약과 보험회사의 승낙으로 이루어집니다.\nExample Result : \n1. 제1조(보험계약의 성립) \n1-1, ① 보험계약은 보험계약자의 청약과 보험회사의 승낙으로 이루어집니다.  \n\nPrevious section Hierachy : {section_number} \n\nContents : \n```\n{contents}\n```"

def parsing_with_llm(section_number, contents):
  return model.predict(prompt=PROMPT_DOC_PARSING.format(section_number=section_number, contents=contents)).text

In [8]:
print(parsing_with_llm('', pages[0].page_content))

 1, 제1조(보험계약의 성립) 
1-1, ① 보험계약은 보험계약자의 청약과 보험회사의 승낙으로 이루어집니다. 
1-2, ② 회사는 계약의 청약을 받고 보험료 전액 (보험료를 일시에 지급하기로 약정한 경우) 또는 제1회 보험료(보험료를 분납하기로 약정한 경우)(이하 ‘ 제1회 보험료 등’ 이라 합니다)를 받


As you can see, the result doesn't seem good. 

We will use manual 

## Test 2. With beautiful Soap



In [9]:
from langchain.document_loaders import PDFMinerPDFasHTMLLoader

loader = PDFMinerPDFasHTMLLoader(target_pdf_file_uri)

data = loader.load()[0]   # entire PDF is loaded as a single Document


In [10]:
from bs4 import BeautifulSoup
soup = BeautifulSoup(data.page_content,'html.parser')
content = soup.find_all('div')

In [11]:
import re
cur_fs = None
cur_text = ''
snippets = []   # first collect all snippets that have the same font size
for c in content:
    sp = c.find('span')
    if not sp:
        continue
    st = sp.get('style')
    if not st:
        continue
    fs = re.findall('font-size:(\d+)px',st)
    if not fs:
        continue
    fs = int(fs[0])
    if not cur_fs:
        cur_fs = fs
    if fs == cur_fs:
        cur_text += c.text
    else:
        snippets.append((cur_text,cur_fs))
        cur_fs = fs
        cur_text = c.text
snippets.append((cur_text,cur_fs))

In [12]:
from langchain.docstore.document import Document
cur_idx = -1
semantic_snippets = []
# Assumption: headings have higher font size than their respective content
for s in snippets:
    # if current snippet's font size > previous section's heading => it is a new heading
    if not semantic_snippets or s[1] > semantic_snippets[cur_idx].metadata['heading_font']:
        metadata={'heading':s[0], 'content_font': 0, 'heading_font': s[1]}
        metadata.update(data.metadata)
        semantic_snippets.append(Document(page_content='',metadata=metadata))
        cur_idx += 1
        continue
    
    # if current snippet's font size <= previous section's content => content belongs to the same section (one can also create
    # a tree like structure for sub sections if needed but that may require some more thinking and may be data specific)
    if not semantic_snippets[cur_idx].metadata['content_font'] or s[1] <= semantic_snippets[cur_idx].metadata['content_font']:
        semantic_snippets[cur_idx].page_content += s[0]
        semantic_snippets[cur_idx].metadata['content_font'] = max(s[1], semantic_snippets[cur_idx].metadata['content_font'])
        continue
    
    # if current snippet's font size > previous section's content but less than previous section's heading than also make a new 
    # section (e.g. title of a PDF will have the highest font size but we don't want it to subsume all sections)
    metadata={'heading':s[0], 'content_font': 0, 'heading_font': s[1]}
    metadata.update(data.metadata)
    semantic_snippets.append(Document(page_content='',metadata=metadata))
    cur_idx += 1

In [ ]:
#for snippet in semantic_snippets:
  #print(snippet)
  #print("###########################################")


## Test 3. Manual Separation

In [90]:
import re

# "제1조" - ① - 1. - (ⅰ)
hierarchy_patterns = [r"^제.*조", r"^[①-⑳]", r"^[0-9]*\.", r"^\([0-9]*\)"]

def check_hierarchy(line):
  for depth in range(len(hierarchy_patterns)):
    if re.search(hierarchy_patterns[depth], line):
       return True, depth + 1
  return False, 0

def make_item(line_cnt, lines):
  item = lines[line_cnt]
  line_cnt = line_cnt + 1
  previous_line = ''
  while line_cnt < len(lines):
    line = lines[line_cnt]
    has_section_mark, cur_depth = check_hierarchy(line)
    if not has_section_mark:
      item = item + line
      line_cnt = line_cnt + 1
      if not line :
        previous_line = line
    else:
      return line_cnt, item, previous_line
  return line_cnt, item, previous_line
    
def add_result(lvl, result_list, depth, number, item):
  result_list.append({ 'depth' : depth, 'number' : number, 'phrase' : item})
  print({ 'level': lvl, 'depth' : depth, 'number' : number, 'phrase' : item})

def parse_hierarchy(lvl, depth, number, line_cnt, lines):
  item = ''
  result = []
  while line_cnt < len(lines):
    line = lines[line_cnt]
    has_section_mark, cur_depth = check_hierarchy(line)
    #if re.search("^제1조", line):
    #  if depth != 0:
    #    return line_cnt - 1, result
    if cur_depth == depth:
      line_cnt, item, previous_line = make_item(line_cnt, lines)
      number = number + 1
      add_result(lvl, result, depth, number, item)
    elif cur_depth > depth:
      line_cnt, child_result = parse_hierarchy(lvl+1, cur_depth, 0, line_cnt, lines)
      result.extend(child_result)
    elif cur_depth < depth or line_cnt < len(lines):
      return line_cnt, result
      
  return line_cnt, result

def parse_documents(pages):
  content = ''
  for page in pages:
    content = content + page.page_content
  lines = content.splitlines()
  return parse_hierarchy(0, 0, 0, 0, lines)



In [ ]:
_, parsed_doc = parse_documents(pages)

In [18]:
def chunk_documents(structured_documents, target_level=2):
  chunk_list = []
  sub_titles = ['','']
  chunk = ''
  for phrase in structured_documents:
    if phrase['depth'] < 2:
      sub_titles[phrase['depth']] = phrase['phrase']
      chunk_list.append('SubTitle:' + sub_titles[0] + '-' + sub_titles[1] + '\n' + chunk)
    else:
      chunk = chunk + '\n' + phrase['phrase']
  return chunk_list
  

In [19]:
chunks = chunk_documents(results)

['SubTitle:LIG주택화재 보험 보통약관    -\n',
 'SubTitle:LIG주택화재 보험 보통약관    -제1조(보험계약의  성립) \n',
 'SubTitle:LIG주택화재 보험 보통약관    -제2조(약관교부  및 설명의무  등) \n\n① 보험계약은  보험계약자의  청약과  보험회사의  승낙으로  이루어집니다 .(이하  “ 보험계약”은  “ 계약”, “ 보험계약자” 는  “ 계약자” , “ 보험회사” 는  “ 회사” 라  합니다 ) \n② 회사는  계약의  청약을  받고  보험료  전액 (보험료를  일시에  지급하기로  약정한  경우 ) 또는  제1회 보험료(보험료를  분납하기로  약정한  경우 )(이하  ‘ 제1회 보험료  등’ 이라  합니다 )를 받은  경우에는  청약일부터 30일 이내에  승낙  또는  거절의  통지를  하며  통지가  없으면  승낙한  것으로  봅니다 . \n③ 회사가  청약을  승낙한  때에는  지체  없이  보험증권 (보험가입증서 )을 계약자에게  교부하여  드리며 , 청약을 거절한  경우에는  거절통지와  함께  받은  금액을  계약자에게  돌려드립니다 . \n④ 이미  성립한  계약을  연장하거나  변경하는  경우에는  회사는  보험증권 (보험가입증서 )에 그 사실을  기재함으로써  보험증권 (보험가입증서 )의 교부에  대신할  수 있습니다 .  ',
 'SubTitle:LIG주택화재 보험 보통약관    -제3조(제1회 보험료  등 및 회사의  보장개시 ) \n\n① 보험계약은  보험계약자의  청약과  보험회사의  승낙으로  이루어집니다 .(이하  “ 보험계약”은  “ 계약”, “ 보험계약자” 는  “ 계약자” , “ 보험회사” 는  “ 회사” 라  합니다 ) \n② 회사는  계약의  청약을  받고  보험료  전액 (보험료를  일시에  지급하기로  약정한  경우 ) 또는  제1회 보험료(보험료를  분납하기로  약정한  경우 )(이하  ‘ 제1회 보험료  등’ 이라  합니다 )를 받은  경우에는  청약일부터 30

In [28]:
import pandas as pd

df_chunks = pd.DataFrame(chunks)
df_chunks.columns = ['context']

In [24]:
from vertexai.preview.language_models import TextEmbeddingModel

model = TextEmbeddingModel.from_pretrained("textembedding-gecko@001")

In [53]:
QUATA_LIMIT = 5

import numpy as np

def make_embeddings(model, sentences):
  context_result_list = []
  for group_cnt in range(0, len(sentences), QUATA_LIMIT):
    embeddings = model.get_embeddings(sentences[group_cnt:group_cnt+5])
    for embedding in embeddings:
      context_result_list.append(embedding.values)
  return np.array(context_result_list)
    

In [54]:
embedding_context = make_embeddings(model, df_chunks['context'].to_list())



In [55]:
embedding_context

array([[ 0.00449999, -0.00301744,  0.00627478, ..., -0.02269317,
         0.01401979, -0.0249997 ],
       [ 0.02074339, -0.01474908,  0.00959441, ..., -0.04234261,
        -0.00165468, -0.03779539],
       [ 0.00172312, -0.00315287,  0.01762285, ..., -0.03959984,
        -0.01853547, -0.04199549],
       ...,
       [-0.01245519,  0.01704678,  0.01230661, ..., -0.04460384,
        -0.03089341, -0.03459932],
       [-0.01360722,  0.01669925,  0.01095967, ..., -0.04419664,
        -0.03096942, -0.03592615],
       [-0.01033744,  0.01590044,  0.01108007, ..., -0.04308092,
        -0.03098719, -0.03743913]])

In [56]:
questions = ['단체계약에서 1년이 지난 보험에 대해서 청약 철회를 할 수 있는가 ?', ## 제5조(청약의 철회) 
             '납일을 하지 않을 경우, 독촉장은 언제 발송되는가?', # 제7조[보험료의 납입연체시 납입최고(독촉)와 계약의 해지] 
             '화재, 폭발에 의한 사고에서 물건을 잊어버렸을 경우, 그 물건에 대한 손해 배상은 가능한가?', # 제12조(보상하지 아니하는 손해)
             '어떤 경우 계약자에 대해서 알려주어야 할 의무가 생기는가?', # 제15조(계약후 알릴 의무)
             '어떤 경우 보험금이 환급되는가 ?' # 제19조(보험료의 환급)
             ] 

df_questions = pd.DataFrame(questions)
df_questions.columns = ['question']

In [57]:
df_questions

question
0             단체계약에서 1년이 지난 보험에 대해서 청약 철회를 할 수 있는가 ?
1                       납일을 하지 않을 경우, 독촉장은 언제 발송되는가?
2  화재, 폭발에 의한 사고에서 물건을 잊어버렸을 경우, 그 물건에 대한 손해 배상은 ...
3                   어떤 경우 계약자에 대해서 알려주어야 할 의무가 생기는가?
4                                 어떤 경우 보험금이 환급되는가 ?

In [58]:
embedding_question = make_embeddings(model, df_questions['question'].to_list())

In [59]:
embedding_question

array([[ 0.02589681,  0.02578002,  0.01141636, ..., -0.03383673,
        -0.06918788, -0.05237233],
       [-0.01118088,  0.0671877 ,  0.00692374, ...,  0.00643602,
        -0.07255773, -0.02344371],
       [-0.00477795,  0.06614242, -0.00139067, ..., -0.00202732,
        -0.06089159, -0.02820396],
       [-0.01270864,  0.05122909,  0.01064137, ...,  0.00037499,
        -0.07340871, -0.02377847],
       [-0.00838485,  0.05777651,  0.01157024, ...,  0.00722593,
        -0.0662403 , -0.01044251]])

In [65]:
import numpy as np

pd.DataFrame(
  np.inner(embedding_context, embedding_question[4:5]),
  columns=['similarity'],
  index=df_chunks
).sort_values('similarity', ascending=False).reset_index()


index  similarity
0    (SubTitle:LIG주택화재 보험 보통약관    -제2조(약관교부  및 설명의무...    0.650245
1    (SubTitle:LIG주택화재 보험 보통약관    -제3조(제1회 보험료  등 및...    0.642401
2    (SubTitle:LIG주택화재 보험 보통약관    -제33조(계약내용의  교환) ...    0.638215
3    (SubTitle:LIG주택화재 보험 보통약관    -제2조(보상하는  손해)   ...    0.637251
4    (SubTitle:LIG주택화재 보험 보통약관    -제15조(계약후  알릴 의무)...    0.636828
..                                                 ...         ...
215  (SubTitle:LIG주택화재 보험 보통약관    -제27조(사기에  의한 계약)...    0.626469
216  (SubTitle:LIG주택화재 보험 보통약관    -제13조(준용규정 ) 이 특별...    0.625252
217  (SubTitle:LIG주택화재 보험 보통약관    -제5조(보험금  등의  지급한...    0.622134
218                 (SubTitle:LIG주택화재 보험 보통약관    -\n,)    0.592801
219  (SubTitle:LIG주택화재 보험 보통약관    -제1조(보험계약의  성립) \n,)    0.585939

[220 rows x 2 columns]

As you can see, there is no matching context in this area.

We will use another model


In [68]:
import requests

API_URL = "https://api-inference.huggingface.co/models/jhgan/ko-sbert-multitask"
headers = {"Authorization" : ""}



In [79]:
from sentence_transformers import SentenceTransformer

def hf_embedding(sentences):
  model = SentenceTransformer('jhgan/ko-sbert-multitask')
  embeddings_list = []
  for i in range(0, len(sentences), 5):
    embeddings = model.encode(sentences[i:i+5])
    for embedding in embeddings:
      embeddings_list.append(embedding.tolist())
  
  return np.array(embeddings_list)


In [80]:
embedding_context_bert = hf_embedding(df_chunks['context'].to_list())

In [81]:
embedding_question_bert = hf_embedding(df_questions['question'].to_list())

In [82]:
embedding_question_bert

array([[-0.30281153, -1.26130939,  0.17991793, ..., -0.28942063,
        -0.79365939, -0.80600518],
       [ 0.20838299, -0.58014745, -0.2540395 , ..., -0.05904411,
        -0.10669541,  0.42982826],
       [-0.2292448 , -0.60557884,  0.00632763, ..., -0.19146068,
        -1.4756    , -0.98911786],
       [ 0.68631333, -0.46605659, -0.08362307, ..., -0.12493642,
        -0.35082054, -0.07842872],
       [ 1.10608196, -0.45971975, -0.63982284, ..., -0.02764811,
        -0.66911542,  0.58380455]])

In [86]:
pd.set_option('display.max_colwidth', None)

question_index = 0
print(df_questions[question_index:question_index+1])

pd.DataFrame(
  np.inner(embedding_context_bert, embedding_question_bert[question_index:question_index+1]),
  columns=['similarity'],
  index=df_chunks
).sort_values('similarity', ascending=False).reset_index()


                                 question
0  단체계약에서 1년이 지난 보험에 대해서 청약 철회를 할 수 있는가 ?


index  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             (SubTitle:LIG주택화재 보험 보통약관    -제7조 (보험기간의  설정)  회사는  새로이  증가  또는  교체되는  피보험자 (보험대상자 )의 보험기간은  보험계약자가  요청하는  기간으로 합니다 . 단, 이 계약기간중  피보험자 (보험대상자 ) 감소의  경우  당해  피보험자 (보험대상자 )의 계약은  해지된  것으로  합니다 .  \n\n① 보험계약은  보험계약자의  청약과  보험회사의  승낙으로  이루어집니다 .(이하  “ 보험계약”은  “ 계약”, “ 보험계약자” 는  “ 계약자” , “ 보험회사” 는  “ 회사” 라  합니다 ) \n② 회사는  계약의  청약을  받고  보험료  전액 (보험료를  일시에  지급하기로  약정한  경우 ) 또는  제1회 보험료(보험료를  분납하기로  약정한  경우 )(이하  ‘ 제1회 보험료  등’ 이라  합니다 )를 받은  경우에는  청약일부터 30일 이내에  승낙  또는  거절의  통지를  하며  통지가  없으면  승낙한  것으로  봅니다 . \n③ 회사가  청약을  승낙한  때에는  지체  없이  보험증권 (보험가입증서 )을 계약자에게  교부하여  드리며 , 청약을 거절한  경우에는  거절통지와  함께  받은  금액을  계약자에게  돌려드립니다 . \n④ 이미  성립한  계약을  연장하거나  변경하는  경우에는  회사는  보험증권 (보험가입증서 )에 그 사실을  기재함으로써  보험증권 (보험가입증서 )의 교부에  대신할  수 있습니다 .  \n① 회사는  계약자가  청약한  경우  계약자에게  약관  및 계약자  보관용  청약서 (청약서  부본 )를 드리고  약관의 중요한  내용을  설명하여  드립니다 . 다만 , 전화 ․우편 ․컴퓨터  등의  통신매체를  통한  보험계약(이하 “ 통신판매  계약” 이라  합니다 )의 경우에는  회사는  계약자의  동의를  얻어  다음  중 한 가지  방법으로  할 수 있습니다 . \n1. 광기록매체  또는  전자우편  등의  전자적  방법으로  약관이나  계약자  보관용  청약서 (청약서  부본 )를 송부하는  방법 . 이 경우  계약자  또는  그 대리인이  이를  수신한  때에  당해  약관이나  계약자  보관용  청약서 (청약서  부본 )를 드린  것으로  봅니다 . \n2. 사이버몰 (컴퓨터를  이용하여  보험거래를  할 수 있도록  설정된  가상의  영업장 )에서 약관  및 그 설명문(약관의  중요한  내용을  알 수 있도록  설명한  문서 )을 읽거나  내려받게  하는  방법 . 이 경우  계약자가 이를  읽거나  내려받은  것을  확인한  때에  당해  약관을  드리고  그 중요한  내용을  설명한  것으로 봅니다 . \n3. 전화를  이용하여  청약내용 , 보험료납입 , 보험기간 , 계약전  알릴의무 , 약관의  중요한  내용  등 계약  체결을  위하여  필요한  사항을  질문  또는  설명하는  방법 . 이 경우  계약자의  답변과  확인내용을  음성  녹음함으로써  약관의  중요한  내용을  설명한  것으로  봅니다 . \n② 회사가  제1항에  의해  제공될  약관  및 계약자  보관용  청약서 (청약서  부본 )를 청약  시 계약자에게  드리지 아니하거나  약관의  중요한  내용을  설명하지  아니한  때 또는  계약을  체결할  때 계약자가  청약서에 자필서명 [날인 (도장을  찍음 ) 또는  전자서명법  제2조 제10호의  규정에  의한  공인인증기관이  인증한 전자서명을  포함합니다 )]을 하지  아니한  때에는  계약자는  계약체결일부터  1개월  이내에  계약을  취소할  수 있습니다 .  \n③ 제2항에  따라  계약이  취소된  경우에는  회사는  이미  납입한  보험료를  계약자에게  돌려드리며 , 보험료를 받은  기간에  대하여  보험개발원이  공시하는  정기예금이율을  연단위  복리로  계산한  금액을  더하여  지급합니다 .  \n① 회사는  계약의  청약을  승낙하고  제1회 보험료  등을  받은  때부터  이 약관이  정한  바에  따라  보장을  합니다 . \n② 회사가  계약자로부터  계약의  청약과  함께  제1회 보험료  등을  받은  경우에  그 청약을  승낙하기  전에  계약에서  정한  보험금  지급사유가  생긴  때에는  회사는  계약상의  보장을  합니다 . \n③ 제2항의  규정에도  불구하고  회사는  다음  중 한 가지에  해당되는  경우에는  보장을  하지  아니합니다 . \n1. 제14조(계약전  알릴  의무 )의 규정에  의하여  계약자  또는  피보험자가  회사에  알린  내용이  보험금  지급사유의  발생에  영향을  미쳤음을  회사가  증명하는  경우  \n2. 제12조(보상하지  아니하는  손해 ), 제16조(계약의  해지 ), 제18조(계약의  무효 ) 또는  제27조(사기에  의한 계약 )의 규정을  준용하여  회사가  보장을  하지  아니할  수 있는  경우  \n④ 계약자가  제1회 보험료  등을  자동이체  또는  신용카드로  납입하는  경우에는  자동이체신청  및 신용카드매출  승인에  필요한  정보를  회사에  제공한  때가  제1회 보험료  등을  납입한  때가  되나 , 계약자의  귀책사유로  자동이체  또는  매출승인이  불가능한  경우에는  제1회 보험료  등이  납입되지  않은  것으로  봅니다 .⑤ 계약이  갱신되는  경우에는  제1항 내지  제3항에  의한  보